In [332]:
import requests

In [127]:
url = "https://mychem.info/v1/chem"
params = {"id":"t32cr1a69r","fields":"drugcentral.approval,ginas.status,ginas.approved"}
params.pop("fields")
#params = {"id":"19150"}

'drugcentral.approval,ginas.status,ginas.approved'

In [128]:
r = requests.get(url,params=params)

In [129]:
print(r.status_code)

200


In [130]:
r.json()

{'_id': 'T32CR1A69R',
 '_version': 1,
 'chembl': {'_license': 'http://bit.ly/2KAUCAm',
  'black_box_warning': 0,
  'chirality': 1,
  'dosed_ingredient': False,
  'drug_indications': [{'efo': [{'id': 'EFO:0001359',
      'term': 'type I diabetes mellitus'}],
    'indication_refs': [{'ClinicalTrials': 'NCT03179423',
      'id': 'NCT03179423',
      'type': 'ClinicalTrials',
      'url': 'https://clinicaltrials.gov/search?id=%22NCT03179423%22'}],
    'max_phase_for_ind': 2,
    'mesh_heading': 'Diabetes Mellitus, Type 1',
    'mesh_id': 'D003922'},
   {'efo': [{'id': 'EFO:0003885', 'term': 'multiple sclerosis'}],
    'indication_refs': [{'ClinicalTrials': 'NCT01699555',
      'id': 'NCT01699555',
      'type': 'ClinicalTrials',
      'url': 'https://clinicaltrials.gov/search?id=%22NCT01699555%22'},
     {'ClinicalTrials': 'NCT03574428',
      'id': 'NCT03574428',
      'type': 'ClinicalTrials',
      'url': 'https://clinicaltrials.gov/search?id=%22NCT03574428%22'},
     {'ClinicalTrials':

In [78]:
import pandas as pd

In [80]:
no_drugs = pd.read_csv("../ara_tables/normalized_drug_names.csv") 

In [82]:

no_drugs["Normalized_Idx"].unique()

array(['PUBCHEM.COMPOUND:25023866', 'PUBCHEM.COMPOUND:119258',
       'NCBIGene:351', ..., 'UMLS:C0439989', 'UMLS:C0120077',
       'UMLS:C0376357'], dtype=object)

In [141]:
none_list = ["UNII", "GTOP"," UMLS","NCBIGene","GTOP"]
def convertDrugIdxToMyChem(idx):
    if(type(idx)==float):
        return None
    if("PUBCHEM" in idx):
        return idx.split(":")[1]
    if("UNII" in idx):
        return idx.split(':')[1] 
    if("CHEMBL" in idx):
        return idx.split(":")[1]
    if("CHEBI" in idx):
        return idx
    if("MESH" in idx):
        return None
    if("GTOP" in idx):
        return None
    if("UMLS" in idx):
        return None
    if("NCBIGene" in idx):
        return None
    if("DRUGBANK" in idx):
        return None
    if("NCBITaxon" in idx):
        return None
    if("DrugCentral" in idx):
        return None
        #The one DC identifier that was being returned was for DrugCentral:5216
    if("UniProtKB" in idx):
        return None
    else:
        raise ValueError(idx)

In [172]:
mychem_query = []
mychem_results = []
no_drug_idx_to_mychem = {}
mychem_to_no_drug = {}


for idx in no_drugs["Normalized_Idx"].unique():
    query_idx = convertDrugIdxToMyChem(idx)
    if(query_idx!=None):
        mychem_query.append(query_idx)
        no_drug_idx_to_mychem[idx] = query_idx
#        print(query_idx)
        if(query_idx in mychem_to_no_drug):
            print('wack',query_idx)
        mychem_to_no_drug[query_idx] = idx
#    if(len(mychem_query)>10):break

In [174]:
len(mychem_query)

94543

In [175]:
url = "https://mychem.info/v1/chem"
params = {"ids":','.join(mychem_query),"fields":"drugcentral.approval,ginas.status,ginas.approved"}
#params.pop("fields")
#params = {"id":"19150"}
r = requests.post(url,params=params)

In [148]:
print(r.status_code)

200


In [157]:
r.json()

[{'query': '25023866', '_id': 'FNALNGZFYGVJKN-UHFFFAOYSA-N', '_version': 1},
 {'query': '119258', '_id': 'ZROGCCBNZBKLEL-MPRHSVQHSA-N', '_version': 1},
 {'query': 'CHEMBL4586086',
  '_id': 'OXELDRCVUWWSFZ-UHFFFAOYSA-N',
  '_version': 1},
 {'query': '77910626', '_id': 'GAQMWPRWVIGRRV-UHFFFAOYSA-N', '_version': 1},
 {'query': '23648106', '_id': 'HLQWEKCWYZMMLL-UHFFFAOYSA-N', '_version': 1},
 {'query': '10115992', '_id': 'AMLKCBXPVBOXAU-UHFFFAOYSA-N', '_version': 1},
 {'query': '222958', '_id': 'IAJKTOIWQHTZOS-UHFFFAOYSA-N', '_version': 1},
 {'query': '442403', '_id': 'HNEGCRMUYSKRRR-NWHWRWDZSA-N', '_version': 1},
 {'query': '21916309', '_id': 'BHDCOZKOHYGBMN-UHFFFAOYSA-N', '_version': 1},
 {'query': 'CHEMBL4760126',
  '_id': 'GZXYMRLGHGNYBT-UHFFFAOYSA-N',
  '_version': 1},
 {'query': '90656659', '_id': 'ARKVONJYFHCBAV-UHFFFAOYSA-N', '_version': 1}]

In [153]:
def divide_chunks(l, n):
    # looping till length l
    for i in range(0, len(l), n):
        yield l[i:i + n]

In [360]:
from tqdm.notebook import tqdm

mychem_results = []
chunk_size=250
fields = ["drugcentral.approval",
        "ginas.status",
        "ginas.approved",
        "ginas.preferred_name",
        "chembl.drug_indications.efo.id",
        "chembl.drug_indications.efo.term",
        "chembl.drug_indications.max_phase_for_ind",
        "chembl.drug_indications.indication_refs.url",
        "chembl.drug_indications.indication_refs.type",
        "chembl.drug_indications.indication_refs"
        "chembl.max_phase",
        "chembl.drug_indications.indication_refs.ClinicalTrials",
        "chembl.drug_indications.indication_refs.FDA"
]
for chunk in tqdm(divide_chunks(mychem_query,chunk_size),total=len(mychem_query)//chunk_size+1):
    params = {"ids":','.join(chunk),"fields":','.join(fields)}
    #params.pop("fields")
    #params = {"id":"19150"}
    r = requests.post(url,params=params)
    mychem_results.extend(r.json())



  0%|          | 0/379 [00:00<?, ?it/s]

In [361]:
print(len(mychem_results))

94675


In [349]:
def safeget(dct, *keys, force_list=True):
    for key in keys:
        try:
            dct = dct[key]
        except KeyError:
            return []
    if(force_list):
        if(type(dct)==list):return dct
        else: return [dct]
    else:
        return dct

def safegetFromList(dct, *keys):
    key_list = [dct]
    for key in keys:
        tmp_key_list = []
        for dct in key_list:
            try:
                dct = dct[key]
            except KeyError:
                return []
            if(type(dct)==list):tmp_key_list.extend(dct)
            else:tmp_key_list.append(dct)
        key_list = tmp_key_list
    return key_list

In [324]:
for x in mychem_results:
    print(x)
    print(x.get('chembl',""))
    if(x.get('chembl',{}).get('max_phase',0)>0):
        print(x)
        break
#mychem_results[0:12]

{'query': '25023866', '_id': 'FNALNGZFYGVJKN-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}
{'query': '119258', '_id': 'ZROGCCBNZBKLEL-MPRHSVQHSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}
{'query': 'CHEMBL4586086', '_id': 'OXELDRCVUWWSFZ-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}
{'query': '77910626', '_id': 'GAQMWPRWVIGRRV-UHFFFAOYSA-N', '_version': 1}

{'query': '23648106', '_id': 'HLQWEKCWYZMMLL-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}
{'query': '10115992', '_id': 'AMLKCBXPVBOXAU-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'_li

In [380]:
def parseMyChem(mychem_result):
    #dc_approvals = mychem_result.get('drugcentral',{}).get('approval',{})
    
    #Drugcentral can return multiple licenses
    dc_approvals = []
    licenses = safeget(mychem_result,'drugcentral',force_list=True)
    for license in licenses:
        #For each license, there can be either a single approval status; or multiple (from FDA, EMA, etc)
        approvals = safeget(license,'approval',force_list=True)
        #if(type(approval)==list): dc_approvals.extend(approval)
        #else:dc_approvals.append(approval)
        dc_approvals.extend(approvals)
    #print(mychem_result)
    #print(licenses)
    #print(dc_approvals)
    fda_approve = ["FDA" == x.get("agency","N/A") for x in dc_approvals ]
    orphan = ['t' == x.get("orphan","N/A") for x in dc_approvals]
    fda_approve = any(fda_approve)
    orphan = any(orphan)
#    if(len(dc_approvals)>1):
#        print(dc_approvals)
#        print(fda_approve)
    ginas_approve = 'approved' == mychem_result.get('ginas',{}).get('status','not approved')
    if(type(mychem_result.get('chembl',{}))==list):
        print(mychem_result)
    max_phase = safegetFromList(mychem_info,"chembl","drug_indications",'max_phase_for_ind')
    if(len(max_phase)==0):max_phase=-1
    else:max_phase=max(max_phase)
    indications = safegetFromList(mychem_result,'chembl','drug_indications')
    return {'fda_approve':fda_approve,'orphan':orphan,'ginas_approve':ginas_approve,"max_phase":max_phase,"indications":indications}


mychem_results[0:10]
mychem_result_dict = {}
cnt = 0
for result in mychem_results:
    mychem_result_dict[result['query']] = result

In [381]:
mychem_result_dict

{'25023866': {'query': '25023866',
  '_id': 'FNALNGZFYGVJKN-UHFFFAOYSA-N',
  '_version': 1},
 '119258': {'query': '119258',
  '_id': 'ZROGCCBNZBKLEL-MPRHSVQHSA-N',
  '_version': 1},
 'CHEMBL4586086': {'query': 'CHEMBL4586086',
  '_id': 'OXELDRCVUWWSFZ-UHFFFAOYSA-N',
  '_version': 1},
 '77910626': {'query': '77910626',
  '_id': 'GAQMWPRWVIGRRV-UHFFFAOYSA-N',
  '_version': 1},
 '23648106': {'query': '23648106',
  '_id': 'HLQWEKCWYZMMLL-UHFFFAOYSA-N',
  '_version': 1},
 '10115992': {'query': '10115992',
  '_id': 'AMLKCBXPVBOXAU-UHFFFAOYSA-N',
  '_version': 1},
 '222958': {'query': '222958',
  '_id': 'IAJKTOIWQHTZOS-UHFFFAOYSA-N',
  '_version': 1},
 '442403': {'query': '442403',
  '_id': 'HNEGCRMUYSKRRR-NWHWRWDZSA-N',
  '_version': 1},
 '21916309': {'query': '21916309',
  '_id': 'BHDCOZKOHYGBMN-UHFFFAOYSA-N',
  '_version': 1},
 'CHEMBL4760126': {'query': 'CHEMBL4760126',
  '_id': 'GZXYMRLGHGNYBT-UHFFFAOYSA-N',
  '_version': 1},
 '90656659': {'query': '90656659',
  '_id': 'ARKVONJYFHCBAV-UH

In [382]:
def getInfoForNoDrugIdx(no_drug_idx,key=None):
    if(no_drug_idx not in no_drug_idx_to_mychem): return False
    mychem_idx = no_drug_idx_to_mychem[no_drug_idx]
    mychem_info = mychem_result_dict[mychem_idx]
    if('fda_approved' not in mychem_info):
        print(mychem_info)
    if(key==None):
        return parseMyChem(mychem_info)
    else:
        return parseMyChem(mychem_info)[key]

In [383]:
#getInfoForNoDrugIdx('PUBCHEM.COMPOUND:25023866')
#no_drug_idx = "PUBCHEM.COMPOUND:6446"
#mychem_idx = no_drug_idx_to_mychem[no_drug_idx]
mychem_info = mychem_result_dict["46871935"]
#licenses = safeget(mychem_info,'drugcentral')
#approvals = licenses[0].get('approval',{})
#l = safegetFromList(mychem_info,'chembl','indications')
#print(mychem_info)
#l
mychem_info

{'query': '46871935',
 '_id': 'XNULRSOGWPFPBL-REWPJTCUSA-N',
 '_version': 1,
 'chembl': [{'_license': 'http://bit.ly/2KAUCAm',
   'drug_indications': [{'efo': [{'id': 'EFO:0001360',
       'term': 'type II diabetes mellitus'}],
     'indication_refs': [{'ClinicalTrials': 'NCT01366287',
       'type': 'ClinicalTrials',
       'url': 'https://clinicaltrials.gov/search?id=%22NCT01366287%22'}],
     'max_phase_for_ind': 1},
    {'efo': [{'id': 'EFO:0000401', 'term': 'diabetic nephropathy'}],
     'indication_refs': [{'ClinicalTrials': 'NCT01488877',
       'type': 'ClinicalTrials',
       'url': 'https://clinicaltrials.gov/search?id=%22NCT01488877%22'}],
     'max_phase_for_ind': 1}]}],
 'ginas': {'_license': '?',
  'approved': 1466088038959,
  'preferred_name': 'PF-03882845',
  'status': 'approved'}}

In [384]:
#print(licenses)
#print(approvals)
getInfoForNoDrugIdx("PUBCHEM.COMPOUND:6446")

#for no_drug_idx in list(no_drug_idx_to_mychem.keys())[0:50]:
#    print(no_drug_idx)
#    print(no_drug_idx,getInfoForNoDrugIdx(no_drug_idx))

{'query': '6446', '_id': 'YLRFCQOZQXIBAB-RBZZARIASA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'drug_indications': [{'efo': [{'id': 'MONDO:0007254', 'term': 'breast cancer'}], 'indication_refs': [{'ClinicalTrials': 'NCT00303615', 'type': 'ClinicalTrials', 'url': 'https://clinicaltrials.gov/search?id=%22NCT00303615%22'}], 'max_phase_for_ind': 2}, {'efo': [{'id': 'MONDO:0002146', 'term': 'hypogonadism'}], 'indication_refs': [{'type': 'DailyMed', 'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c194-5650-4d1f-9e28-8cea038cce81'}], 'max_phase_for_ind': 4}, {'efo': [{'id': 'EFO:0000616', 'term': 'neoplasm'}], 'indication_refs': [{'type': 'DailyMed', 'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c194-5650-4d1f-9e28-8cea038cce81'}], 'max_phase_for_ind': 4}, {'efo': [{'id': 'EFO:1001078', 'term': 'orchitis'}], 'indication_refs': [{'type': 'DailyMed', 'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c194-5650-4d

{'fda_approve': True,
 'orphan': False,
 'ginas_approve': True,
 'max_phase': 1,
 'indications': [{'efo': [{'id': 'MONDO:0007254', 'term': 'breast cancer'}],
   'indication_refs': [{'ClinicalTrials': 'NCT00303615',
     'type': 'ClinicalTrials',
     'url': 'https://clinicaltrials.gov/search?id=%22NCT00303615%22'}],
   'max_phase_for_ind': 2},
  {'efo': [{'id': 'MONDO:0002146', 'term': 'hypogonadism'}],
   'indication_refs': [{'type': 'DailyMed',
     'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c194-5650-4d1f-9e28-8cea038cce81'}],
   'max_phase_for_ind': 4},
  {'efo': [{'id': 'EFO:0000616', 'term': 'neoplasm'}],
   'indication_refs': [{'type': 'DailyMed',
     'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c194-5650-4d1f-9e28-8cea038cce81'}],
   'max_phase_for_ind': 4},
  {'efo': [{'id': 'EFO:1001078', 'term': 'orchitis'}],
   'indication_refs': [{'type': 'DailyMed',
     'url': 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=5328c1

In [305]:
keys = ['fda_approve', 'orphan', 'ginas_approve','max_phase']
for k in keys:
    no_drugs[k] = no_drugs.apply(lambda x: getInfoForNoDrugIdx(x.Normalized_Idx,k),axis=1)

{'query': '25023866', '_id': 'FNALNGZFYGVJKN-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'query': '25023866', '_id': 'FNALNGZFYGVJKN-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
[]
[]
{'query': '119258', '_id': 'ZROGCCBNZBKLEL-MPRHSVQHSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'query': '119258', '_id': 'ZROGCCBNZBKLEL-MPRHSVQHSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
[]
[]
{'query': 'CHEMBL4586086', '_id': 'OXELDRCVUWWSFZ-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
{'query': 'CHEMBL4586086', '_id': 'OXELDRCVUWWSFZ-UHFFFAOYSA-N', '_version': 1, 'chembl': {'_license': 'http://bit.ly/2KAUCAm', 'max_phase': 0}}
[]
[]
{'query': '77910626', '_id': 'GAQMWPRWVIGRRV-UHFFFAOYSA-N', '_version': 1}
{'query': '77910626', '_id': 'GAQMWPRWVIGRRV-UHFFFAOYSA-N', '

Traceback (most recent call last):
  File "/home/ubuntu/miniconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py", line 3442, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_3282285/1594843440.py", line 3, in <module>
    no_drugs[k] = no_drugs.apply(lambda x: getInfoForNoDrugIdx(x.Normalized_Idx,k),axis=1)
  File "/home/ubuntu/miniconda3/lib/python3.9/site-packages/pandas/core/frame.py", line 9565, in apply
    args=args,
  File "/home/ubuntu/miniconda3/lib/python3.9/site-packages/pandas/core/apply.py", line 746, in apply
    elif isinstance(self.f, np.ufunc):
  File "/home/ubuntu/miniconda3/lib/python3.9/site-packages/pandas/core/apply.py", line 873, in apply_standard
    # must be a scalar or 1d
  File "/home/ubuntu/miniconda3/lib/python3.9/site-packages/pandas/core/apply.py", line 889, in apply_series_generator
  File "/tmp/ipykernel_3282285/1594843440.py", line 3, in <lambda>
    no_drugs[k] = no_drugs.apply(lambda x: getInfo

In [299]:
no_drugs[no_drugs.orphan]

Original_Idx             Normalized_Idx  \
135     CHEMBL.COMPOUND:CHEMBL1469      PUBCHEM.COMPOUND:4775   
864          PUBCHEM.COMPOUND:2123      PUBCHEM.COMPOUND:2123   
1142     PUBCHEM.COMPOUND:16222096  PUBCHEM.COMPOUND:16222096   
1158               UNII:T4H8FMA7IM            UNII:T4H8FMA7IM   
1275         PUBCHEM.COMPOUND:3406      PUBCHEM.COMPOUND:3406   
...                            ...                        ...   
130579             UNII:8GZG754X6M            UNII:8GZG754X6M   
130705     PUBCHEM.COMPOUND:439693    PUBCHEM.COMPOUND:439693   
130898   PUBCHEM.COMPOUND:16220172  PUBCHEM.COMPOUND:16220172   
131216               UMLS:C0026056      PUBCHEM.COMPOUND:4192   
131778    PUBCHEM.COMPOUND:5282411   PUBCHEM.COMPOUND:5282411   

              Normalized_Name  fda_approve  orphan  ginas_approve  
135      4-Phenylbutyric acid         True    True           True  
864               Altretamine         True    True           True  
1142              Cobimetinib         True    True           True  
1158               SILTUXIMAB         True    True          False  
1275               Fomepizole         True    True           True  
...                       ...          ...     ...            ...  
130579  GEMTUZUMAB OZOGAMICIN         True    True          False  
130705            Pentostatin         True    True           True  
130898              Ivacaftor         True    True           True  
131216              Midazolam         True    True           True  
131778           Epoprostenol         True    True          False  

[1045 rows x 6 columns]

In [300]:
no_drugs[no_drugs.fda_approve]

Original_Idx              Normalized_Idx  \
14      CHEMBL.COMPOUND:CHEMBL1445       PUBCHEM.COMPOUND:6446   
18      CHEMBL.COMPOUND:CHEMBL1471  PUBCHEM.COMPOUND:135413536   
42           PUBCHEM.COMPOUND:5988       PUBCHEM.COMPOUND:5988   
87                   UMLS:C0527379       PUBCHEM.COMPOUND:2540   
103           PUBCHEM.COMPOUND:838        PUBCHEM.COMPOUND:838   
...                            ...                         ...   
131724      PUBCHEM.COMPOUND:60657      PUBCHEM.COMPOUND:60657   
131735     PUBCHEM.COMPOUND:516900     PUBCHEM.COMPOUND:516900   
131745      PUBCHEM.COMPOUND:72078      PUBCHEM.COMPOUND:72078   
131754   PUBCHEM.COMPOUND:11750009   PUBCHEM.COMPOUND:11750009   
131778    PUBCHEM.COMPOUND:5282411    PUBCHEM.COMPOUND:5282411   

                       Normalized_Name  fda_approve  orphan  ginas_approve  
14                     Fluoxymesterone         True   False           True  
18                          Aprepitant         True   False           True  
42                             Sucrose         True   False           True  
87               Candesartan cilexetil         True   False           True  
103                      DL-Adrenaline         True   False          False  
...                                ...          ...     ...            ...  
131724                   Levobetaxolol         True   False           True  
131735           Potassium perchlorate         True   False           True  
131745          Prednisolone phosphate         True   False           True  
131754  Cortexolone 17alpha-propionate         True   False           True  
131778                    Epoprostenol         True    True          False  

[6296 rows x 6 columns]

In [301]:
no_drugs.to_excel("normalized_drugs_with_approval_from_mychem.xlsx")

In [250]:
no_drug_idx="PUBCHEM.COMPOUND:359"
mychem_idx = no_drug_idx_to_mychem[no_drug_idx]
mychem_info = mychem_result_dict[mychem_idx]

In [251]:
mychem_info

{'query': '359',
 '_id': 'QCDYQQDYXPDABM-UHFFFAOYSA-N',
 '_version': 1,
 'ginas': {'_license': '?',
  'approved': 1466087920350,
  'preferred_name': 'PHLOROGLUCINOL',
  'status': 'approved'}}

In [386]:
indication_rows = []
for no_drug_idx in no_drug_idx_to_mychem:
    mychem_idx = no_drug_idx_to_mychem[no_drug_idx]
    mychem_info = mychem_result_dict[mychem_idx]
    if(type(mychem_info.get('chembl',{})) == list):
        print(mychem_info)

    parsed = parseMyChem(mychem_info)
    indications = parsed["indications"]
    if(len(indications)>0):
        for i,indication in enumerate(indications):
            #print(indications)
            disease_idx = safegetFromList(indication,'efo','id')
            disease_name = safegetFromList(indication,'efo','term')
            ind_refs = safegetFromList(indication,'indication_refs')
            ref_output = []
            for ref in ind_refs:
                if('ClinicalTrials' in ref):ref_output.append(ref['ClinicalTrials'])
                else:ref_output.append(ref.get('url','N/A'))
            #trials = safegetFromList(indication,'indication_refs','ClinicalTrials')
            max_phase = indication.get('max_phase_for_ind',-1)
            
            indication_rows.append((no_drug_idx,disease_idx,disease_name,max_phase,ref_output))
            #print(no_drug_idx,i,trials,disease_idx,disease_name,max_phase)
            #print(indication)

{'query': '46871935', '_id': 'XNULRSOGWPFPBL-REWPJTCUSA-N', '_version': 1, 'chembl': [{'_license': 'http://bit.ly/2KAUCAm', 'drug_indications': [{'efo': [{'id': 'EFO:0001360', 'term': 'type II diabetes mellitus'}], 'indication_refs': [{'ClinicalTrials': 'NCT01366287', 'type': 'ClinicalTrials', 'url': 'https://clinicaltrials.gov/search?id=%22NCT01366287%22'}], 'max_phase_for_ind': 1}, {'efo': [{'id': 'EFO:0000401', 'term': 'diabetic nephropathy'}], 'indication_refs': [{'ClinicalTrials': 'NCT01488877', 'type': 'ClinicalTrials', 'url': 'https://clinicaltrials.gov/search?id=%22NCT01488877%22'}], 'max_phase_for_ind': 1}]}], 'ginas': {'_license': '?', 'approved': 1466088038959, 'preferred_name': 'PF-03882845', 'status': 'approved'}}
{'query': '46871935', '_id': 'XNULRSOGWPFPBL-REWPJTCUSA-N', '_version': 1, 'chembl': [{'_license': 'http://bit.ly/2KAUCAm', 'drug_indications': [{'efo': [{'id': 'EFO:0001360', 'term': 'type II diabetes mellitus'}], 'indication_refs': [{'ClinicalTrials': 'NCT01366

In [350]:
trials = safegetFromList(indication,'indication_refs','ClinicalTrials')

In [351]:
trials

[]

In [369]:
mychem_info

{'query': '46871935',
 '_id': 'XNULRSOGWPFPBL-REWPJTCUSA-N',
 '_version': 1,
 'chembl': [{'_license': 'http://bit.ly/2KAUCAm',
   'drug_indications': [{'efo': [{'id': 'EFO:0001360',
       'term': 'type II diabetes mellitus'}],
     'indication_refs': [{'ClinicalTrials': 'NCT01366287',
       'type': 'ClinicalTrials',
       'url': 'https://clinicaltrials.gov/search?id=%22NCT01366287%22'}],
     'max_phase_for_ind': 1},
    {'efo': [{'id': 'EFO:0000401', 'term': 'diabetic nephropathy'}],
     'indication_refs': [{'ClinicalTrials': 'NCT01488877',
       'type': 'ClinicalTrials',
       'url': 'https://clinicaltrials.gov/search?id=%22NCT01488877%22'}],
     'max_phase_for_ind': 1}]}],
 'ginas': {'_license': '?',
  'approved': 1466088038959,
  'preferred_name': 'PF-03882845',
  'status': 'approved'}}

In [376]:
for no_drug_idx in no_drug_idx_to_mychem:
    mychem_idx = no_drug_idx_to_mychem[no_drug_idx]
    mychem_info = mychem_result_dict[mychem_idx]
    if(type(mychem_info.get('chembl',{})) == list):
#        print(mychem_info)
        max(safegetFromList(mychem_info,"chembl","drug_indications",'max_phase_for_ind'))

In [388]:
df = pd.DataFrame(indication_rows,columns=['chem','disease','term','max_phase','support'])

In [389]:
df

chem           disease  \
0              PUBCHEM.COMPOUND:6446   [MONDO:0007254]   
1              PUBCHEM.COMPOUND:6446   [MONDO:0002146]   
2              PUBCHEM.COMPOUND:6446     [EFO:0000616]   
3              PUBCHEM.COMPOUND:6446     [EFO:1001078]   
4         PUBCHEM.COMPOUND:135413536     [EFO:0003829]   
...                              ...               ...   
47307      PUBCHEM.COMPOUND:11750009     [EFO:0003894]   
47308      PUBCHEM.COMPOUND:11750009     [EFO:0004191]   
47309  CHEMBL.COMPOUND:CHEMBL4297553  [Orphanet:79213]   
47310  CHEMBL.COMPOUND:CHEMBL3545054     [EFO:0000183]   
47311  CHEMBL.COMPOUND:CHEMBL3545054     [EFO:0000311]   

                          term  max_phase  \
0              [breast cancer]          2   
1               [hypogonadism]          4   
2                   [neoplasm]          4   
3                   [orchitis]          4   
4         [alcohol dependence]          2   
...                        ...        ...   
47307                   [acne]          3   
47308  [androgenetic alopecia]          2   
47309  [Mucopolysaccharidosis]          1   
47310      [Hodgkins lymphoma]          2   
47311                 [cancer]          1   

                                                 support  
0                                          [NCT00303615]  
1      [http://dailymed.nlm.nih.gov/dailymed/drugInfo...  
2      [http://dailymed.nlm.nih.gov/dailymed/drugInfo...  
3      [http://dailymed.nlm.nih.gov/dailymed/drugInfo...  
4                             [NCT01176591, NCT02210195]  
...                                                  ...  
47307  [NCT01631474, NCT02682264, NCT02608476, NCT026...  
47308                                      [NCT02279823]  
47309  [NCT03053089, NCT03071341, NCT02597114, NCT023...  
47310                                      [NCT02456675]  
47311                                      [NCT01905813]  

[47312 rows x 5 columns]

In [391]:
for x in indication_rows:
    if(len(x[1])!=1):
       print(x)
       

('PUBCHEM.COMPOUND:135413536', ['HP:0002018', 'EFO:0006911'], ['Nausea', 'Chemotherapy-induced nausea and vomiting'], 4, ['NCT00619359', 'NCT00990821', 'NCT02205164', 'NCT03219710', 'NCT01111851', 'NCT03079219', 'NCT03245918', 'NCT02097823', 'NCT02979548', 'NCT00337727', 'NCT03237611', 'http://www.whocc.no/atc_ddd_index/?code=A04AD12', 'NCT00092196', 'NCT00952341', 'NCT01402024', 'NCT00818259', 'NCT01362530', 'NCT01474915', 'NCT00475085', 'http://dailymed.nlm.nih.gov/dailymed/drugInfo.cfm?setid=d72e0e10-4557-41b0-b65d-d395468cad19', 'NCT01376297', 'NCT00945321', 'NCT02484911', 'NCT02933099', 'NCT02336750', 'NCT04912271', 'NCT04437017'])
('PUBCHEM.COMPOUND:135413536', ['EFO:0006911', 'EFO:0004888', 'HP:0002017'], ['Chemotherapy-induced nausea and vomiting', 'post operative nausea and vomiting', 'Nausea and vomiting'], 4, ['NCT00990821', 'NCT00738621', 'NCT04013386', 'NCT02431286', 'NCT02357693', 'NCT00090155', 'NCT01897337', 'NCT02021851', 'NCT00169572', 'NCT00659945', 'NCT03435003', 'h

In [394]:
mychem_result_dict["176870"]['chembl']['drug_indications']

[{'efo': [{'id': 'EFO:0000571', 'term': 'lung adenocarcinoma'}],
  'indication_refs': [{'ClinicalTrials': 'NCT03076164',
    'type': 'ClinicalTrials',
    'url': 'https://clinicaltrials.gov/search?id=%22NCT03076164%22'},
   {'ClinicalTrials': 'NCT00716456',
    'type': 'ClinicalTrials',
    'url': 'https://clinicaltrials.gov/search?id=%22NCT00716456%22'}],
  'max_phase_for_ind': 1},
 {'efo': [{'id': 'EFO:1000026', 'term': 'diffuse intrinsic pontine glioma'}],
  'indication_refs': [{'ClinicalTrials': 'NCT02233049',
    'type': 'ClinicalTrials',
    'url': 'https://clinicaltrials.gov/search?id=%22NCT02233049%22'},
   {'ClinicalTrials': 'NCT01182350',
    'type': 'ClinicalTrials',
    'url': 'https://clinicaltrials.gov/search?id=%22NCT01182350%22'}],
  'max_phase_for_ind': 2},
 {'efo': [{'id': 'MONDO:0016691', 'term': 'pilocytic astrocytoma'},
   {'id': 'MONDO:0016693', 'term': 'subependymal giant cell astrocytoma'},
   {'id': 'EFO:0002499', 'term': 'anaplastic astrocytoma'}],
  'indicati

In [397]:
df.to_excel("drug_indications.xlsx")